<a href="https://colab.research.google.com/github/mobassir94/comprehensive-bangla-tts/blob/main/mlt_TTS_inference_demo/Multilingual_(ben%2Bara)_tts_inference_colab_demo.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

Based on our previous [notebook](https://github.com/mobassir94/comprehensive-bangla-tts/blob/main/mlt_TTS_inference_demo/bn-ar-tts-pipeline.ipynb)

In [1]:
%%capture
! pip install -U pip
! pip install TTS==0.8.0
! pip install bnnumerizer
! pip install bangla==0.0.2

In [2]:
import torch

device = torch.device("cuda" if torch.cuda.is_available() else "cpu") #need cuda
male = False
device

device(type='cuda')

# Arabic tacotron2 TTS

In [3]:
!git clone https://github.com/nipponjo/tts-arabic-tacotron2


Cloning into 'tts-arabic-tacotron2'...
remote: Enumerating objects: 54, done.
remote: Counting objects: 100% (54/54), done.
remote: Compressing objects: 100% (50/50), done.
remote: Total 54 (delta 1), reused 54 (delta 1), pack-reused 0
Unpacking objects: 100% (54/54), done.


In [4]:
import sys
sys.path.append('/content/tts-arabic-tacotron2')
import gdown
from model.networks import Tacotron2Wave
from IPython.display import Audio
import soundfile as sf
import shutil
import bangla

In [5]:
url = "https://drive.google.com/drive/folders/196xZbqqxzsBQdKr1UKdh_wL_9qtJkt6u?usp=sharing"
gdown.download_folder(url=url, quiet=False, use_cookies=False)  

Retrieving folder list


Retrieving folder 1uHomQ-7dxwTc8DagzSjIIdCHiSEncROE UNIVERSAL_V1
Processing file 1_uRBHf9VmK6CGoB9c0Jb6nE8Gah7X6WI config.json
Processing file 1ejejcJ2l9AL0AnP79Ag-XK3HZzBYW64h do_02500000
Processing file 1oUGwFAAsRnM3OfwSWJVFJKyBmBZHc4fp g_02500000
Processing file 1CMvxg7zP1xoJbCLaJTbBCf1YU1SHl4uT tacotron2_ar.pth
Building directory structure completed


Retrieving folder list completed
Building directory structure
Downloading...
From: https://drive.google.com/uc?id=1_uRBHf9VmK6CGoB9c0Jb6nE8Gah7X6WI
To: /content/arabic_tts/UNIVERSAL_V1/config.json
100%|██████████| 799/799 [00:00<00:00, 1.61MB/s]
Downloading...
From: https://drive.google.com/uc?id=1ejejcJ2l9AL0AnP79Ag-XK3HZzBYW64h
To: /content/arabic_tts/UNIVERSAL_V1/do_02500000
100%|██████████| 960M/960M [00:07<00:00, 126MB/s]
Downloading...
From: https://drive.google.com/uc?id=1oUGwFAAsRnM3OfwSWJVFJKyBmBZHc4fp
To: /content/arabic_tts/UNIVERSAL_V1/g_02500000
100%|██████████| 55.8M/55.8M [00:00<00:00, 110MB/s]
Downloading...
From: https://drive.google.com/uc?id=1CMvxg7zP1xoJbCLaJTbBCf1YU1SHl4uT
To: /content/arabic_tts/tacotron2_ar.pth
100%|██████████| 338M/338M [00:02<00:00, 167MB/s]
Download completed


['/content/arabic_tts/UNIVERSAL_V1/config.json',
 '/content/arabic_tts/UNIVERSAL_V1/do_02500000',
 '/content/arabic_tts/UNIVERSAL_V1/g_02500000',
 '/content/arabic_tts/tacotron2_ar.pth']

In [6]:
shutil.copy('/content/arabic_tts/UNIVERSAL_V1/config.json', './tts-arabic-tacotron2/pretrained/hifigan-universal-v1')

shutil.copy('/content/arabic_tts/UNIVERSAL_V1/do_02500000', './tts-arabic-tacotron2/pretrained/hifigan-universal-v1')

shutil.copy('/content/arabic_tts/UNIVERSAL_V1/g_02500000', './tts-arabic-tacotron2/pretrained/hifigan-universal-v1')

shutil.copy('/content/arabic_tts/tacotron2_ar.pth', './tts-arabic-tacotron2/pretrained')

model_sd_path = './tts-arabic-tacotron2/pretrained/tacotron2_ar.pth'
# vocoder
vocoder_state_path = './tts-arabic-tacotron2/pretrained/hifigan-universal-v1/g_02500000'

vocoder_config_path = './tts-arabic-tacotron2/pretrained/hifigan-universal-v1/config.json'

In [7]:
%%writefile /content/tts-arabic-tacotron2/utils/__init__.py
import sys
import yaml
try:
    from yaml import CLoader as Loader
except ImportError:
    from yaml import Loader


class DictConfig(object):
    """Creates a Config object from a dict 
       such that object attributes correspond to dict keys.    
    """

    def __init__(self, config_dict):
        self.__dict__.update(config_dict)

    def __str__(self):
        return '\n'.join(f"{key}: {val}" for key, val in self.__dict__.items())

    def __repr__(self):
        return self.__str__()


def get_custom_config(fname):
    with open(fname, 'r') as stream:
        config_dict = yaml.load(stream, Loader)
    config = DictConfig(config_dict)
    return config


def get_basic_config():
    return get_custom_config('./tts-arabic-tacotron2/configs/basic.yaml')


def get_config(fname):
    config = get_basic_config()
    custom_config = get_custom_config(fname)

    config.__dict__.update(custom_config.__dict__)
    return config


def read_lines_from_file(path, encoding='utf-8'):
    lines = []
    with open(path, 'r', encoding=encoding) as f:
        for line in f:
            lines.append(line.strip())
    return lines


def progbar(iterable, length=30, symbol='='):
    """Wrapper generator function for an iterable. 
       Prints a progressbar when yielding an item. \\
       Args:
          iterable: an object supporting iteration
          length: length of the progressbar
    """
    n = len(iterable)
    for i, item in enumerate(iterable):
        steps = length*(i+1) // n
        sys.stdout.write('\r')
        sys.stdout.write(f"[{symbol*steps:{length}}] {(100/n*(i+1)):.1f}%")
        if i == (n-1):
            sys.stdout.write('\n')
        sys.stdout.flush()
        yield item

Overwriting /content/tts-arabic-tacotron2/utils/__init__.py


In [8]:
ar_model = Tacotron2Wave(model_sd_path = model_sd_path,vocoder_sd = vocoder_state_path, vocoder_config = vocoder_config_path)
#ar_model = ar_model.cuda()
ar_model = ar_model.to(device) 

#Bangla GlowTTS

In [9]:
try:
  from TTS.utils.synthesizer import Synthesizer
except:
  print("coundn't import TTS synthesizer,trying again!")
import TTS
from TTS.utils.synthesizer import Synthesizer
TTS.__version__

coundn't import TTS synthesizer,trying again!


'0.8.0'

In [10]:
# link -> hhttps://drive.google.com/drive/folders/1IMCiQpyYBqu98dlRMSINjFNc34fI6zhs?usp=sharing
url = "https://drive.google.com/drive/folders/1IMCiQpyYBqu98dlRMSINjFNc34fI6zhs?usp=sharing"
gdown.download_folder(url=url, quiet=True, use_cookies=False)   


if(male):
  test_ckpt = '/content/bangla_tts/bn_glow_tts/male/checkpoint_39000.pth'
  test_config = '/content/bangla_tts/bn_glow_tts/male/config.json'
else:
  test_ckpt = '/content/bangla_tts/bn_glow_tts/female/checkpoint_180000.pth'
  test_config = '/content/bangla_tts/bn_glow_tts/female/config.json'

bn_model=Synthesizer(test_ckpt,test_config)


 > Using model: glow_tts
 > Setting up Audio Processor...
 | > sample_rate:22050
 | > resample:True
 | > num_mels:80
 | > log_func:np.log10
 | > min_level_db:-100
 | > frame_shift_ms:None
 | > frame_length_ms:None
 | > ref_level_db:20
 | > fft_size:1024
 | > power:1.5
 | > preemphasis:0.0
 | > griffin_lim_iters:60
 | > signal_norm:True
 | > symmetric_norm:True
 | > mel_fmin:0
 | > mel_fmax:None
 | > pitch_fmin:1.0
 | > pitch_fmax:640.0
 | > spec_gain:20.0
 | > stft_pad_mode:reflect
 | > max_norm:4.0
 | > clip_norm:True
 | > do_trim_silence:True
 | > trim_db:45
 | > do_sound_norm:False
 | > do_amp_to_db_linear:True
 | > do_amp_to_db_mel:True
 | > do_rms_norm:False
 | > db_level:None
 | > stats_path:None
 | > base:10
 | > hop_length:256
 | > win_length:1024


#TTS BigTextToAudio

In [11]:
import re
import torchaudio.functional as F
from bnnumerizer import numerize
"""
TODO: 
    * debug and traceback options
    
"""

class BigTextToAudio(object):
    
    def __init__(self,
                 ar_model,
                 bn_model,
                 ar_sample_rate=22050,
                 bn_sample_rate=48000,
                 out_sample_rate=22050,
                 attribution_dict={"সাঃ":"সাল্লাল্লাহু আলাইহি ওয়া সাল্লাম",                   
                                  "আঃ":"আলাইহিস সালাম",
                                  "রাঃ":"রাদিআল্লাহু আনহু",
                                  "রহঃ":"রহমাতুল্লাহি আলাইহি",
                                  "রহিঃ":"রহিমাহুল্লাহ",
                                  "হাফিঃ":"হাফিযাহুল্লাহ",
                                  "দাঃবাঃ":"দামাত বারাকাতুহুম,দামাত বারাকাতুল্লাহ"},
                text_batch_size=1024,
                resample_params={"lowpass_filter_width": 64,
                                "rolloff": 0.9475937167399596,
                                "resampling_method": "kaiser_window",
                                "beta": 14.769656459379492}
                ):
        '''
            Instantiates a Big Text to Audio conversion object for bangla and arabic
            args:
                ar_model : arabic tts model
                bn_model : bangla tts model
                ar_sample_rate : arabic audio sample rate [optional] default: 22050
                bn_sample_rate : bangla audio sample rate [optional] default: 48000
                out_sample_rate : audio sample rate [optional] default: 22050
                attribution_dict : a dict for attribution expansion [optional]
                text_batch_size : chunk of long text to be considered as batch [optional]
                resample_params : audio resampling parameters [optional]
            resources:
                # Main class: modified from https://github.com/snakers4/silero-models/pull/174
                # Audio converter:https://www.kaggle.com/code/shahruk10/inference-notebook-wav2vec2
        '''
        self.ar_model = ar_model
        self.bn_model = bn_model
        self.attribution_dict=attribution_dict
        self.batch_size=text_batch_size
        self.ar_sample_rate=ar_sample_rate
        self.bn_sample_rate=bn_sample_rate
        self.sample_rate=out_sample_rate  
        self.resample_params=resample_params
        
    # public
    def ar_tts(self,text):
        '''
            args: 
                text: arabic text (string)
            returns:
                audio as torch tensor
        '''
        return self.ar_model.tts(text)
    # public
    def bn_tts(self,text):
        '''
            args: 
                text   : bangla text (string)
            returns:
                audio as torch tensor
        '''
        return torch.as_tensor(self.bn_model.tts(text))
    
    # public
    def expand_full_attribution(self,text):
        '''
            expands full attribution
        '''
        for k,v in self.attribution_dict.items():text=text.replace(k,v)
        return text
    
    # public
    def tag_text(self,text):
        '''
            * tags arabic text with <ar>text</ar>
            * tags bangla text with <bn>text</bn>
        '''
        # remove multiple spaces
        text=re.sub(' +', ' ',text)
        # create start and end
        text="start"+text+"end"
        # tag text
        parts=re.split(u'[\u0600-\u06FF]+', text)
        # remove non chars
        parts=[p for p in parts if p.strip()]
        # unique parts
        parts=set(parts)
        # tag the text
        for m in parts:
            if len(m.strip())>1:text=text.replace(m,f"</ar><SPLIT><bn>{m}</bn><SPLIT><ar>")
        # clean-tags
        text=text.replace("</ar><SPLIT><bn>start",'<bn>')
        text=text.replace("end</bn><SPLIT><ar>",'</bn>')
        return text

    # private
    def __batch_text(self,text):
        '''
            batches a given text based on batch size
        '''
        batch=[]
        if len(text)<self.batch_size:
            batch=[text]
        else:
            for idx in range(0,len(text),self.batch_size):
                batch.append(text[idx:min(idx + self.batch_size, len(text))])
        return batch

    
    def process_text(self,text):
        '''
            private function to process text
                * expand attributions
                * numerize text
                * tag sections of the text
                * sequentially list text blocks
                * batch blocks
        '''
        # expand attributes
        text=self.expand_full_attribution(text)
        # english numbers to bangla conversion
        res = re.search('[0-9]', text)
        if res is not None:
          text = bangla.convert_english_digit_to_bangla_digit(text)
        # numerize text
        text=numerize(text)
        # tag sections
        text=self.tag_text(text)
        # text blocks
        blocks=text.split("<SPLIT>")
        blocks=[b for b in blocks if b.strip()]
        # create tuple of (lang,text)
        data=[]
        for block in blocks:
            lang=None
            if "<bn>" in block:
                block=block.replace("<bn>",'').replace("</bn>",'')
                lang="bn"
            elif "<ar>" in block:
                block=block.replace("<ar>",'').replace("</ar>",'')
                lang="ar"
            # create batches
            if lang:
                batch=self.__batch_text(block)
                for _text in batch:
                    if _text.strip():
                        data.append((lang,_text))
        return data
    
    def resample_audio(self,audio,sr):
        '''
            resample audio with sample rate
            args:
                audio : torch.tensor audio
                sr: audi sample rate
        '''
        if sr==self.sample_rate:
            return audio
        else:
            return F.resample(audio,sr,self.sample_rate,**self.resample_params)
        
    
    def get_audio(self,data):
        '''
            creates audio from given data 
                * data=List[Tuples(lang,text)]
        '''
        audio_list = []
        for block in data:
            lang,text=block
            if lang=="bn":
                audio=self.bn_tts(text)
                sr=self.bn_sample_rate
            else:
                audio=self.ar_tts(text)
                sr=self.ar_sample_rate
            
            if self.resample_audio_to_out_sample_rate:
                audio=self.resample_audio(audio,sr)
                
            audio_list.append(audio)
        audio = torch.cat([k for k in audio_list])
        return audio
    
    # call
    def __call__(self,text,resample_audio_to_out_sample_rate=True):
        '''
            args: 
                text   : bangla text (string)
                resample_audio_to_out_sample_rate: for different sample rate in different models, resample the output audio 
                                                   in uniform sample rate 
                                                   * default:True
            returns:
                audio as numpy data
        '''
        self.resample_audio_to_out_sample_rate=resample_audio_to_out_sample_rate
        data=self.process_text(text)
        audio=self.get_audio(data)
        return audio.detach().cpu().numpy()

#check textprocessing

In [12]:
text = '''[1] الحَمد এর মধ্যে যে ال রয়েছে, তা استغراق (সমূদয়) অথবা اختصاص (নির্দিষ্টীকরণ)এর অর্থে ব্যবহার হয়েছে। 
অর্থাৎ, সমস্ত প্রশংসা আল্লাহর জন্যই বা তাঁর জন্য নির্দিষ্ট; কেননা প্রশংসার প্রকৃত অধিকারী একমাত্র মহান আল্লাহই।
 কারো মধ্যে যদি কোন গুণ, সৌন্দর্য এবং কৃতিত্ব থাকে, তবে তাও মহান আল্লাহ কর্তৃক সৃষ্ট। অতএব প্রশংসার অধিকারী তিনিই। 
 ‘আল্লাহ’ শব্দটি মহান আল্লাহর সত্তার এমন এক সতন্ত্র নাম যার ব্যবহার অন্য কারো জন্য করা বৈধ নয়। 
 ‘আলহামদু লিল্লাহ’ কৃতজ্ঞতা-জ্ঞাপক বাক্য। এর বহু ফযীলতের কথা হাদীসসমূহে এসেছে। 
 একটি হাদীসে ‘লা-ইলাহা ইল্লাল্লা-হ’কে উত্তম জিকির বলা হয়েছে এবং ‘আলহামদু লিল্লাহ’কে উত্তম দুআ বলা হয়েছে। 
 (তিরমিযী, নাসায়ী ইত্যাদি) সহীহ মুসলিম এবং নাসায়ীর বর্ণনায় এসেছে, ‘আলহামদু লিল্লাহ’ দাঁড়িপাল্লা ভর্তি করে দেয়।
  এ জন্যই অন্য এক বর্ণনায় এসেছে যে, আল্লাহ এটা পছন্দ করেন যে, প্রত্যেক পানাহারের পর বান্দা তাঁর প্রশংসা করুক। 
  (সহীহ মুসলিম)[2] رَبّ মহান আল্লাহর সুন্দর নামসমূহের অন্যতম। যার অর্থ হল, প্রত্যেক জিনিসকে সৃষ্টি ক’রে তার প্রয়োজনীয় জিনিসের ব্যবস্থা ক’রে তাকে পরিপূর্ণতা দানকারী। 
  কোন জিনিসের প্রতি সম্বন্ধ (ইযাফত) না করে এর ব্যবহার অন্য কারো জন্য বৈধ নয়। عَالَمِيْن عَالَم (বিশ্ব-জাহান) শব্দের বহুবচন। তবে সকল সৃষ্টির সমষ্টিকে عَالَم বলা হয়। 
  এই জন্যেই এর বহুবচন ব্যবহার হয় না। কিন্তু এখানে তাঁর (আল্লাহর) পূর্ণ প্রতিপালকত্ব প্রকাশের জন্য এরও বহুবচন ব্যবহার করা হয়েছে। 
  এ থেকে উদ্দেশ্য হল, সৃষ্টির ভিন্ন ভিন্ন শ্রেণী বা সম্প্রদায়। যেমন, জ্বিন সম্প্রদায়, মানব সম্প্রদায়, ফিরিশ্তাকুল এবং জীব-জন্তু ও পশু-পক্ষীকুল ইত্যাদি। 
  এই সমস্ত সৃষ্টির প্রয়োজনসমূহও একে অপর থেকে অবশ্যই ভিন্নতর। কিন্তু বিশ্ব-প্রতিপালক প্রত্যেকের অবস্থা, 
  পরিস্থিতি এবং প্রকৃতি ও দেহ অনুযায়ী তার প্রয়োজনীয় জিনিসের ব্যবস্থা করে থাকেন।তাফসীরে আহসানুল বায়ান'''



MLT_TTS=BigTextToAudio(ar_model=ar_model,
                   bn_model=bn_model)

data=MLT_TTS.process_text(text)
data

[('bn', '[এক] '),
 ('ar', 'الحَمد'),
 ('bn', ' এর মধ্যে যে '),
 ('ar', 'ال'),
 ('bn', ' রয়েছে, তা '),
 ('ar', 'استغراق'),
 ('bn', ' (সমূদয়) অথবা '),
 ('ar', 'اختصاص'),
 ('bn',
  ' (নির্দিষ্টীকরণ)এর অর্থে ব্যবহার হয়েছে। \nঅর্থাৎ, সমস্ত প্রশংসা আল্লাহর জন্যই বা তাঁর জন্য নির্দিষ্ট; কেননা প্রশংসার প্রকৃত অধিকারী একমাত্র মহান আল্লাহই।\n কারো মধ্যে যদি কোন গুণ, সৌন্দর্য এবং কৃতিত্ব থাকে, তবে তাও মহান আল্লাহ কর্তৃক সৃষ্ট। অতএব প্রশংসার অধিকারী তিনিই। \n ‘আল্লাহ’ শব্দটি মহান আল্লাহর সত্তার এমন এক সতন্ত্র নাম যার ব্যবহার অন্য কারো জন্য করা বৈধ নয়। \n ‘আলহামদু লিল্লাহ’ কৃতজ্ঞতা-জ্ঞাপক বাক্য। এর বহু ফযীলতের কথা হাদীসসমূহে এসেছে। \n একটি হাদীসে ‘লা-ইলাহা ইল্লাল্লা-হ’কে উত্তম জিকির বলা হয়েছে এবং ‘আলহামদু লিল্লাহ’কে উত্তম দুআ বলা হয়েছে। \n (তিরমিযী, নাসায়ী ইত্যাদি) সহীহ মুসলিম এবং নাসায়ীর বর্ণনায় এসেছে, ‘আলহামদু লিল্লাহ’ দাঁড়িপাল্লা ভর্তি করে দেয়।\n এ জন্যই অন্য এক বর্ণনায় এসেছে যে, আল্লাহ এটা পছন্দ করেন যে, প্রত্যেক পানাহারের পর বান্দা তাঁর প্রশংসা করুক। \n (সহীহ মুসলিম)[দুই] '),
 ('ar', 'رَبّ'),


In [13]:
audio=MLT_TTS(text,resample_audio_to_out_sample_rate=False)
Audio(audio, rate=MLT_TTS.sample_rate)

 > Text splitted to sentences.
['[এক]']
[এক]
 [!] Character '[' not found in the vocabulary. Discarding it.
[এক]
 [!] Character ']' not found in the vocabulary. Discarding it.
 > Processing time: 1.0860857963562012
 > Real-time factor: 1.6111539161500428
 > Text splitted to sentences.
['এর মধ্যে যে']
 > Processing time: 0.5032472610473633
 > Real-time factor: 0.45122812728100037
 > Text splitted to sentences.
['রয়েছে, তা']
 > Processing time: 0.7464368343353271
 > Real-time factor: 0.5949585091488565
 > Text splitted to sentences.
['(সমূদয়) অথবা']
(সমূদয়) অথবা
 [!] Character '(' not found in the vocabulary. Discarding it.
(সমূদয়) অথবা
 [!] Character ')' not found in the vocabulary. Discarding it.
 > Processing time: 0.6467709541320801
 > Real-time factor: 0.4094309697580491
 > Text splitted to sentences.
['(নির্দিষ্টীকরণ)এর অর্থে ব্যবহার হয়েছে।', 'অর্থাৎ, সমস্ত প্রশংসা আল্লাহর জন্যই বা তাঁর জন্য নির্দিষ্ট; কেননা প্রশংসার প্রকৃত অধিকারী একমাত্র মহান আল্লাহই।', 'কারো মধ্যে যদি কোন গুণ, স